In [1]:
import nltk
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold
import  time
nltk.download('brown')
nltk.download('universal_tagset')
from nltk.corpus import brown
brown_tagged =brown.tagged_sents( tagset='universal')
# print(brown_news_tagged)
# brown_train = brown_news_tagged[100:]

[nltk_data] Downloading package brown to /root/nltk_data...
[nltk_data]   Unzipping corpora/brown.zip.
[nltk_data] Downloading package universal_tagset to /root/nltk_data...
[nltk_data]   Unzipping taggers/universal_tagset.zip.


In [2]:
def tag_seq(t2, t1, train):
    tags_list = [pair[1] for pair in train]
    count=tag_fd[t1]
    count_t2=0
    for i in range(0,len(tags_list)-1):
        if tags_list[i]==t1 and tags_list[i+1] == t2:
            count_t2 += 1
    return count_t2/count

In [3]:
def word_tag(word, tag, train ):
#     tag_list=[]
#     for i in train:
#         if(i[1]==tag):
#             tag_list.append(i)
    count_tag = tag_fd[tag]
    count=word_tag_fd[(word,tag)]
    return count/count_tag

In [4]:
def Viterbi(words, train_bag):
    state = []
    T = list(set([pair[1] for pair in train_bag]))
    print(T)
    hmm_final_chain=[]
    for key, word in enumerate(words):
        prob_col = [] 
        if word in wordset:
          for tag in T:
              if word_tag_fd.get((words[key], tag)) == None:
                  emis_prob_word=0
              else:
                  emis_prob_word = words_df.loc[words[key],tag]

              if key == 0:
                  trans_prob_word = tags_df.loc['.', tag]
              else:
                  trans_prob_word = tags_df.loc[state[-1], tag]   
              prob_col.append(trans_prob_word*emis_prob_word)    
          pmax = max(prob_col)
          hmm_chain = T[prob_col.index(pmax)]  
        else:
          for tag in T:
              if key == 0:
                  trans_prob_word = tags_df.loc['.', tag]
              else:
                  trans_prob_word = tags_df.loc[state[-1], tag]   
              prob_col.append(trans_prob_word)    
          pmax = max(prob_col)
          hmm_chain = T[prob_col.index(pmax)]
          
        state.append(hmm_chain)
        hmm_final_chain.append((word,hmm_chain)) 
    return hmm_final_chain



In [5]:
##brown_train,brown_test =train_test_split(brown_tagged,train_size=0.80,test_size=0.20,random_state = 102)
#print(len(brown_train))
#print(len(brown_test))
#kf=KFold(n_splits=5)
len_brown_data=len(brown_tagged)/5
acuracy_avg=0
confusion_mat=[]
per_pos_acc=[]

for i in range(5):
  first_part=int(i*(len_brown_data))
  second_part=int((i+1)*len_brown_data)
  brown_train=brown_tagged[:first_part]+brown_tagged[second_part:]
  brown_test =brown_tagged[first_part:second_part]
  #train_test_split(brown_tagged,train_size=0.80,test_size=0.20,random_state = 50+(10*i))

  brown_train_words= [ tup for sent in brown_train for tup in sent ]

  tag_fd = nltk.FreqDist(tag for (word, tag) in brown_train_words)
  word_fd=nltk.FreqDist(word for (word, tag) in brown_train_words)
  word_tag_fd=nltk.FreqDist((word, tag) for (word, tag) in brown_train_words)
  print(tag_fd.keys())
  print(len(word_tag_fd.keys()))
  tagset=tag_fd.keys()
  wordset=word_fd.keys()
  print(word_fd['A'])
  print(brown_train_words[0])
  for i in tagset:
    print(tag_fd[i])
  print(word_tag_fd.keys())
  tags_matrix = np.zeros((len(tagset), len(tagset)), dtype='float32')
  for i, t1 in enumerate(list(tagset)):
      for j, t2 in enumerate(list(tagset)): 
          tags_matrix[i, j] = tag_seq(t2, t1,brown_train_words)
  word_tag_matrix = np.zeros((len(wordset), len(tagset)), dtype='float32')
  for i, t1 in enumerate(list(wordset)):
     for j, t2 in enumerate(list(tagset)): 
        word_tag_matrix[i, j] = word_tag(t1, t2,brown_train_words) 
  print(word_tag_matrix)
  tags_df = pd.DataFrame(tags_matrix, columns = list(tagset),index=list(tagset))
  display(tags_df)
  words_df=pd.DataFrame(word_tag_matrix,columns=list(tagset),index=list(wordset))
  display(words_df)
  test_run_base = [tup for sent in brown_test for tup in sent]
 
# list of untagged words
  test_tagged_words = [tup[0] for sent in brown_test for tup in sent]
  start = time.time()
  tagged_seq = Viterbi(test_tagged_words,brown_train_words)
  end = time.time()
  difference = end-start
 
  print("Time taken in seconds: ", difference)
 
# accuracy
  check = [i for i, j in zip(tagged_seq, test_run_base) if i == j] 
# confusion_mat=np.zeros()
  conf_matrix = np.zeros((len(tagset), len(tagset)), dtype='float32')
  for i, t1 in enumerate(list(tagset)):
    for j, t2 in enumerate(list(tagset)): 
        conf_matrix[i, j] = len([p for p,q in zip(tagged_seq,test_run_base) if p[1]==t1 and q[1]==t2])
  confusion_mat.append(conf_matrix)
  perPOSAcc=np.zeros(len(list(tagset)))
  req_arr=[]
  taglist=list(tagset)
  for ind, val in enumerate (perPOSAcc):
    val=conf_matrix[ind][ind]/np.sum(conf_matrix[:][ind])
    req_arr.append((taglist[ind],val))
  print(req_arr)
  per_pos_acc.append(req_arr)
 
 
  accuracy = len(check)/len(tagged_seq)
  acuracy_avg=acuracy_avg+accuracy
  print('Viterbi Algorithm Accuracy: ',accuracy*100)


dict_keys(['ADP', 'PRON', 'VERB', 'NOUN', '.', 'DET', 'CONJ', 'ADV', 'ADJ', 'PRT', 'NUM', 'X'])
50753
1006
('If', 'ADP')
113718
41130
145622
208768
117450
107564
30489
45268
64780
24038
10900
1105
dict_keys([('If', 'ADP'), ('we', 'PRON'), ('return', 'VERB'), ('to', 'ADP'), ('them', 'PRON'), ('today', 'NOUN'), (',', '.'), ('have', 'VERB'), ('no', 'DET'), ('difficulty', 'NOUN'), ('spotting', 'VERB'), ('their', 'DET'), ('weaknesses', 'NOUN'), ('but', 'CONJ'), ('find', 'VERB'), ('still', 'ADV'), ('pleasing', 'ADJ'), ('.', '.'), ('Records', 'NOUN'), ('sound', 'VERB'), ('like', 'ADP'), ('records', 'NOUN'), ('because', 'ADP'), ('they', 'PRON'), ('provide', 'VERB'), ('a', 'DET'), ('different', 'ADJ'), ('sort', 'NOUN'), ('of', 'ADP'), ('experience', 'NOUN'), ('than', 'ADP'), ('live', 'ADJ'), ('music', 'NOUN'), ('This', 'DET'), ('difference', 'NOUN'), ('is', 'VERB'), ('made', 'VERB'), ('up', 'PRT'), ('many', 'ADJ'), ('factors', 'NOUN'), ('Some', 'DET'), ('are', 'VERB'), ('obvious', 'ADJ'), ('suc

ADP      PRON      VERB      NOUN         .       DET      CONJ  \
ADP   0.020621  0.074307  0.041814  0.252062  0.009269  0.459021  0.002040   
PRON  0.056650  0.007829  0.701556  0.008947  0.107586  0.018186  0.011403   
VERB  0.170318  0.058803  0.182143  0.094841  0.083058  0.159413  0.014936   
NOUN  0.248836  0.020367  0.163598  0.133268  0.289815  0.016492  0.061743   
.     0.110975  0.113989  0.092771  0.125858  0.147654  0.145075  0.089630   
DET   0.009074  0.010208  0.065403  0.630546  0.012764  0.005652  0.000697   
CONJ  0.073404  0.071567  0.203778  0.234117  0.020630  0.149464  0.000230   
ADV   0.142750  0.050742  0.236061  0.031192  0.178360  0.071397  0.018114   
ADJ   0.090939  0.004307  0.018200  0.646712  0.103026  0.005851  0.038669   
PRT   0.091605  0.007613  0.613820  0.034321  0.083410  0.082411  0.013312   
NUM   0.131560  0.009817  0.047431  0.383670  0.272477  0.014495  0.040550   
X     0.048869  0.008145  0.047964  0.041629  0.276018  0.005430  0.024434   

           ADV       ADJ       PRT       NUM         X  
ADP   0.015934  0.081570  0.014571  0.028289  0.000501  
PRON  0.053173  0.009531  0.024070  0.001045  0.000024  
VERB  0.104572  0.057066  0.066494  0.008179  0.000179  
NOUN  0.027581  0.012315  0.017982  0.007712  0.000292  
.     0.080868  0.039932  0.034338  0.017437  0.001464  
DET   0.017125  0.236417  0.002101  0.008646  0.001367  
CONJ  0.091771  0.110138  0.025550  0.018761  0.000590  
ADV   0.096602  0.133295  0.028629  0.012790  0.000066  
ADJ   0.010327  0.056360  0.019574  0.005557  0.000479  
PRT   0.037774  0.018928  0.011981  0.004784  0.000042  
NUM   0.017248  0.055963  0.005046  0.021560  0.000183  
X     0.006335  0.002715  0.008145  0.000000  0.530317

ADP      PRON      VERB      NOUN    .       DET  CONJ  \
If             0.005048  0.000000  0.000000  0.000000  0.0  0.000000   0.0   
we             0.000000  0.036178  0.000000  0.000000  0.0  0.000000   0.0   
return         0.000000  0.000000  0.000439  0.000398  0.0  0.000000   0.0   
to             0.076505  0.000000  0.000000  0.000000  0.0  0.000000   0.0   
them           0.000000  0.035667  0.000000  0.000000  0.0  0.000084   0.0   
...                 ...       ...       ...       ...  ...       ...   ...   
olive-flushed  0.000000  0.000000  0.000000  0.000000  0.0  0.000000   0.0   
Cherokee       0.000000  0.000000  0.000000  0.000005  0.0  0.000000   0.0   
coral-colored  0.000000  0.000000  0.000000  0.000000  0.0  0.000000   0.0   
boucle         0.000000  0.000000  0.000000  0.000005  0.0  0.000000   0.0   
stupefying     0.000000  0.000000  0.000007  0.000000  0.0  0.000000   0.0   

                    ADV       ADJ       PRT  NUM         X  
If             0.000000  0.000000  0.000000  0.0  0.000000  
we             0.000000  0.000000  0.000000  0.0  0.000000  
return         0.000000  0.000031  0.000000  0.0  0.000000  
to             0.000022  0.000000  0.481571  0.0  0.002715  
them           0.000000  0.000000  0.000000  0.0  0.000905  
...                 ...       ...       ...  ...       ...  
olive-flushed  0.000000  0.000015  0.000000  0.0  0.000000  
Cherokee       0.000000  0.000000  0.000000  0.0  0.000000  
coral-colored  0.000000  0.000015  0.000000  0.0  0.000000  
boucle         0.000000  0.000000  0.000000  0.0  0.000000  
stupefying     0.000000  0.000000  0.000000  0.0  0.000000  

[47402 rows x 12 columns]

['PRON', 'VERB', 'PRT', 'NOUN', 'ADP', 'NUM', 'DET', 'ADJ', '.', 'ADV', 'X', 'CONJ']
Time taken in seconds:  47.84721517562866
[('ADP', 0.9208384), ('PRON', 0.99572486), ('VERB', 0.94426227), ('NOUN', 0.94849485), ('.', 0.85031766), ('DET', 0.93955976), ('CONJ', 0.990517), ('ADV', 0.9148259), ('ADJ', 0.90780497), ('PRT', 0.7287092), ('NUM', 0.97586685), ('X', 0.79710144)]
Viterbi Algorithm Accuracy:  92.28391116791819
dict_keys(['DET', 'NOUN', 'ADJ', 'VERB', 'ADP', '.', 'ADV', 'CONJ', 'PRT', 'PRON', 'NUM', 'X'])
51836
1029
('The', 'DET')
106635
214875
64037
144750
112491
117828
44210
29510
24144
40748
11758
1122
dict_keys([('The', 'DET'), ('Fulton', 'NOUN'), ('County', 'NOUN'), ('Grand', 'ADJ'), ('Jury', 'NOUN'), ('said', 'VERB'), ('Friday', 'NOUN'), ('an', 'DET'), ('investigation', 'NOUN'), ('of', 'ADP'), ("Atlanta's", 'NOUN'), ('recent', 'ADJ'), ('primary', 'NOUN'), ('election', 'NOUN'), ('produced', 'VERB'), ('``', '.'), ('no', 'DET'), ('evidence', 'NOUN'), ("''", '.'), ('that', 'AD

DET      NOUN       ADJ      VERB       ADP         .       ADV  \
DET   0.005908  0.630468  0.235110  0.064941  0.009171  0.012604  0.017330   
NOUN  0.016214  0.153647  0.013119  0.160759  0.242695  0.282085  0.026336   
ADJ   0.006059  0.649218  0.057092  0.016787  0.088652  0.103534  0.010025   
VERB  0.160870  0.096145  0.056470  0.184912  0.167427  0.082701  0.102570   
ADP   0.456170  0.257558  0.080664  0.039879  0.020171  0.009699  0.015663   
.     0.144719  0.136071  0.039337  0.090157  0.107445  0.150236  0.077206   
ADV   0.071635  0.032956  0.132866  0.239335  0.140534  0.176838  0.095793   
CONJ  0.149780  0.239038  0.107997  0.196001  0.073873  0.021959  0.091562   
PRT   0.083126  0.034294  0.019011  0.612119  0.094185  0.081635  0.038726   
PRON  0.017620  0.009399  0.009105  0.702047  0.055095  0.107686  0.054236   
NUM   0.013693  0.369280  0.060640  0.044480  0.132420  0.285423  0.022453   
X     0.005348  0.061497  0.003565  0.051693  0.048128  0.263815  0.008021   

          CONJ       PRT      PRON       NUM         X  
DET   0.000600  0.002138  0.010034  0.010222  0.001472  
NOUN  0.058318  0.018015  0.019644  0.008800  0.000368  
ADJ   0.037603  0.019192  0.004060  0.007386  0.000390  
VERB  0.013976  0.067447  0.058722  0.008553  0.000207  
ADP   0.001805  0.014570  0.073855  0.029576  0.000391  
.     0.087042  0.034050  0.113521  0.018697  0.001511  
ADV   0.017666  0.029247  0.050351  0.012712  0.000068  
CONJ  0.000271  0.026127  0.073839  0.019011  0.000542  
PRT   0.012757  0.011846  0.007331  0.004887  0.000083  
PRON  0.011485  0.024026  0.008295  0.000982  0.000025  
NUM   0.036996  0.005358  0.007399  0.021602  0.000255  
X     0.022282  0.008913  0.005348  0.000891  0.520499

...

DET      NOUN       ADJ      VERB  ADP    .  ADV  CONJ  \
The            0.052852  0.000000  0.000000  0.000000  0.0  0.0  0.0   0.0   
Fulton         0.000000  0.000074  0.000000  0.000000  0.0  0.0  0.0   0.0   
County         0.000000  0.000300  0.000000  0.000000  0.0  0.0  0.0   0.0   
Grand          0.000000  0.000000  0.000213  0.000000  0.0  0.0  0.0   0.0   
Jury           0.000000  0.000017  0.000000  0.000000  0.0  0.0  0.0   0.0   
...                 ...       ...       ...       ...  ...  ...  ...   ...   
olive-flushed  0.000000  0.000000  0.000014  0.000000  0.0  0.0  0.0   0.0   
lineage        0.000000  0.000004  0.000000  0.000000  0.0  0.0  0.0   0.0   
coral-colored  0.000000  0.000000  0.000014  0.000000  0.0  0.0  0.0   0.0   
boucle         0.000000  0.000004  0.000000  0.000000  0.0  0.0  0.0   0.0   
stupefying     0.000000  0.000000  0.000000  0.000007  0.0  0.0  0.0   0.0   

               PRT  PRON  NUM         X  
The            0.0   0.0  0.0  0.000000  
Fulton         0.0   0.0  0.0  0.000000  
County         0.0   0.0  0.0  0.000000  
Grand          0.0   0.0  0.0  0.002562  
Jury           0.0   0.0  0.0  0.000000  
...            ...   ...  ...       ...  
olive-flushed  0.0   0.0  0.0  0.000000  
lineage        0.0   0.0  0.0  0.000000  
coral-colored  0.0   0.0  0.0  0.000000  
boucle         0.0   0.0  0.0  0.000000  
stupefying     0.0   0.0  0.0  0.000000  

[51034 rows x 12 columns]

['PRON', 'VERB', 'PRT', 'NOUN', 'ADP', 'NUM', 'DET', 'ADJ', '.', 'ADV', 'X', 'CONJ']
Time taken in seconds:  41.45845341682434
[('DET', 0.88169783), ('NOUN', 0.95082194), ('ADJ', 0.9078271), ('VERB', 0.9542055), ('ADP', 0.91328734), ('.', 0.9585466), ('ADV', 0.92527694), ('CONJ', 0.9919477), ('PRT', 0.7400269), ('PRON', 0.9933091), ('NUM', 0.9538754), ('X', 0.7407407)]
Viterbi Algorithm Accuracy:  93.16605358687929
dict_keys(['DET', 'NOUN', 'ADJ', 'VERB', 'ADP', '.', 'ADV', 'CONJ', 'PRT', 'PRON', 'NUM', 'X'])
54944
1148
('The', 'DET')
116989
241528
73866
150459
126332
118482
45940
32177
23316
35550
13802
1205
dict_keys([('The', 'DET'), ('Fulton', 'NOUN'), ('County', 'NOUN'), ('Grand', 'ADJ'), ('Jury', 'NOUN'), ('said', 'VERB'), ('Friday', 'NOUN'), ('an', 'DET'), ('investigation', 'NOUN'), ('of', 'ADP'), ("Atlanta's", 'NOUN'), ('recent', 'ADJ'), ('primary', 'NOUN'), ('election', 'NOUN'), ('produced', 'VERB'), ('``', '.'), ('no', 'DET'), ('evidence', 'NOUN'), ("''", '.'), ('that', 'ADP')

DET      NOUN       ADJ      VERB       ADP         .       ADV  \
DET   0.006197  0.619041  0.245297  0.065639  0.009522  0.012711  0.017950   
NOUN  0.016454  0.155758  0.013444  0.155705  0.251511  0.277044  0.024900   
ADJ   0.005537  0.664311  0.057740  0.017627  0.087104  0.092059  0.008854   
VERB  0.163639  0.102347  0.060362  0.189287  0.174586  0.074745  0.103649   
ADP   0.452625  0.265491  0.088085  0.042752  0.019267  0.009918  0.015309   
.     0.159839  0.144756  0.046075  0.094993  0.121478  0.118583  0.078847   
ADV   0.076317  0.034393  0.143165  0.248106  0.144623  0.153135  0.099216   
CONJ  0.153246  0.260310  0.119153  0.182211  0.076079  0.020574  0.089909   
PRT   0.081103  0.038514  0.018013  0.655601  0.085306  0.062232  0.028435   
PRON  0.017328  0.007961  0.009958  0.717131  0.055949  0.093333  0.053755   
NUM   0.013694  0.371613  0.057890  0.045935  0.130996  0.286480  0.019490   
X     0.005809  0.050622  0.003320  0.049793  0.053112  0.258921  0.005809   

          CONJ       PRT      PRON       NUM         X  
DET   0.000650  0.001778  0.009591  0.010266  0.001359  
NOUN  0.059480  0.017518  0.018698  0.009138  0.000352  
ADJ   0.037027  0.018777  0.003168  0.007338  0.000460  
VERB  0.014562  0.061532  0.045368  0.009744  0.000179  
ADP   0.001876  0.013813  0.058085  0.032320  0.000459  
.     0.089912  0.027920  0.094960  0.021210  0.001418  
ADV   0.016217  0.027819  0.042142  0.014780  0.000087  
CONJ  0.000280  0.023029  0.054791  0.019952  0.000466  
PRT   0.010165  0.009264  0.005661  0.005618  0.000086  
PRON  0.010717  0.024248  0.008692  0.000928  0.000000  
NUM   0.037893  0.005434  0.008405  0.022026  0.000145  
X     0.019917  0.005809  0.005809  0.000830  0.540249

DET      NOUN       ADJ  VERB  ADP    .  ADV  CONJ  PRT  \
The            0.054962  0.000000  0.000000   0.0  0.0  0.0  0.0   0.0  0.0   
Fulton         0.000000  0.000070  0.000000   0.0  0.0  0.0  0.0   0.0  0.0   
County         0.000000  0.000335  0.000000   0.0  0.0  0.0  0.0   0.0  0.0   
Grand          0.000000  0.000000  0.000176   0.0  0.0  0.0  0.0   0.0  0.0   
Jury           0.000000  0.000012  0.000000   0.0  0.0  0.0  0.0   0.0  0.0   
...                 ...       ...       ...   ...  ...  ...  ...   ...  ...   
Anta           0.000000  0.000008  0.000000   0.0  0.0  0.0  0.0   0.0  0.0   
Freya          0.000000  0.000008  0.000000   0.0  0.0  0.0  0.0   0.0  0.0   
Norberg        0.000000  0.000008  0.000000   0.0  0.0  0.0  0.0   0.0  0.0   
Scandinavians  0.000000  0.000004  0.000000   0.0  0.0  0.0  0.0   0.0  0.0   
steam-baths    0.000000  0.000004  0.000000   0.0  0.0  0.0  0.0   0.0  0.0   

               PRON  NUM        X  
The             0.0  0.0  0.00000  
Fulton          0.0  0.0  0.00000  
County          0.0  0.0  0.00000  
Grand           0.0  0.0  0.00249  
Jury            0.0  0.0  0.00000  
...             ...  ...      ...  
Anta            0.0  0.0  0.00000  
Freya           0.0  0.0  0.00000  
Norberg         0.0  0.0  0.00000  
Scandinavians   0.0  0.0  0.00000  
steam-baths     0.0  0.0  0.00000  

[51461 rows x 12 columns]

['PRON', 'VERB', 'PRT', 'NOUN', 'ADP', 'NUM', 'DET', 'ADJ', '.', 'ADV', 'X', 'CONJ']
Time taken in seconds:  35.090928077697754
[('DET', 0.861262), ('NOUN', 0.94410545), ('ADJ', 0.87281924), ('VERB', 0.9545215), ('ADP', 0.8969955), ('.', 0.9702095), ('ADV', 0.9180993), ('CONJ', 0.9870561), ('PRT', 0.7645212), ('PRON', 0.997617), ('NUM', 0.87344915), ('X', 0.6603774)]
Viterbi Algorithm Accuracy:  92.76602073303735


In [6]:
print("Viterbi Algorithm Accuracy after 5 iterations: ",acuracy_avg*20)  


Viterbi Algorithm Accuracy after 5 iterations:  92.75957754935578


In [7]:
# print(confusion_mat)
confusion_mat_avg=np.array(confusion_mat)
conf_ma_avg=np.sum(confusion_mat,axis=0)/5
print(conf_ma_avg.shape)
conf_df = pd.DataFrame(conf_ma_avg, columns = list(tagset),index=list(tagset))
display(conf_df)
# confusion_np=np.array((len(list(tagset)),(list(tagset)),5))
# for ind,i in enumerate(confusion_mat):
  # print()
  # print("Confusion matrix for ",ind,"th iteration is : ")
  # conf_df = pd.DataFrame(i, columns = list(tagset),index=list(tagset))
  # display(conf_df)
  # ind=np.array()



(12, 12)


DET          NOUN           ADJ          VERB           ADP  \
DET   27138.400391   1385.000000    214.600006    186.800003     34.599998   
NOUN      1.400000  38967.601562    901.400024   1086.000000      8.600000   
ADJ       2.000000    474.399994  18019.400391    406.200012     21.200001   
VERB      3.800000   1033.800049    533.000000  39209.398438     26.799999   
ADP     188.800003      5.400000     94.599998    880.400024  27185.599609   
.         7.400000   1375.400024    176.600006    487.399994     11.800000   
ADV      10.200000     25.000000    365.600006     17.400000    185.199997   
CONJ     44.799999      0.600000      3.000000      7.200000     22.799999   
PRT       1.400000      8.000000     71.599998    174.000000   1269.199951   
PRON    323.399994      2.600000      0.600000      5.800000      0.000000   
NUM       0.400000     97.199997      0.000000     16.600000      0.200000   
X         0.400000     19.400000      1.200000      5.200000      0.600000   

                 .          ADV         CONJ          PRT         PRON  \
DET      44.000000    97.000000   121.599998    32.599998   471.200012   
NOUN      5.200000    44.400002     1.800000    24.600000     1.000000   
ADJ       0.000000   532.799988    16.200001    95.599998     2.600000   
VERB      0.800000    89.800003    11.200000   272.399994     6.400000   
ADP       0.200000   440.399994    13.800000   923.799988   268.399994   
.     29323.599609    47.400002    12.800000    36.599998     2.800000   
ADV       2.000000  9161.200195    13.600000    17.600000     0.600000   
CONJ      0.200000    24.400000  7962.000000   120.400002     4.000000   
PRT       0.000000   148.199997   115.199997  7066.000000    16.000000   
PRON      0.200000     0.400000    23.799999     5.200000  8611.000000   
NUM       0.000000     0.000000     0.000000     0.800000     0.000000   
X         4.800000     0.000000     0.000000     0.200000     0.200000   

              NUM          X  
DET     77.400002  26.600000  
NOUN    37.200001  60.599998  
ADJ     12.000000   4.600000  
VERB    55.799999  32.599998  
ADP     24.000000  17.799999  
.       99.199997  46.200001  
ADV      0.000000   1.000000  
CONJ     0.000000   0.800000  
PRT      0.000000   1.200000  
PRON     0.000000   1.400000  
NUM   2668.600098   1.000000  
X        0.600000  83.400002

In [8]:
prec=[]
recall=[]
# for i in range(len(list(tagset)):
for i, tag in enumerate(list(tagset)):
  prec.append((tag,conf_ma_avg[i][i]/np.sum(conf_ma_avg[i,:])))
  # print(np.sum(conf_ma_avg[i,:]))

  # print(tag)
  
  recall.append((tag,conf_ma_avg[i][i]/np.sum(conf_ma_avg[:,i])))
  # print(np.sum(conf_ma_avg[:,i]))
  print("--"*10)
prec=dict(prec)
recall=dict(recall)
print(prec)
print(recall)


--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
--------------------
{'DET': 0.90977484, 'NOUN': 0.9471996, 'ADJ': 0.9199674, 'VERB': 0.9499367, 'ADP': 0.9048836, '.': 0.92716396, 'ADV': 0.93487364, 'CONJ': 0.97213745, 'PRT': 0.796546, 'PRON': 0.959507, 'NUM': 0.95827353, 'X': 0.71896553}
{'DET': 0.97893393, 'NOUN': 0.8979869, 'ADJ': 0.8841014, 'VERB': 0.92295635, 'ADP': 0.94504046, '.': 0.9980464, 'ADV': 0.8654071, 'CONJ': 0.96020263, 'PRT': 0.82202935, 'PRON': 0.9176062, 'NUM': 0.8970687, 'X': 0.30086583}


In [9]:
brown_tagged_words= [ tup for sent in brown_tagged for tup in sent ]
tags_fd = nltk.FreqDist(tag for (word, tag) in brown_tagged_words)
# for i,j in zip()
sump=0
sumr=0
for i in list(tagset):
  sump=sump+(tags_fd[i]*prec[i])
  sumr=sumr+(tags_fd[i]*recall[i])

sump=sump/len(brown_tagged_words)
sumr=sumr/len(brown_tagged_words)
print("Precision : ",sump)
print("Recall : ",sumr)

Precision :  0.930173842295186
Recall :  0.9276729483750239


In [10]:
# print(2*sump*sumr/(sump+sumr))
sumf1=2*sump*sumr/(sump+sumr)
# sumf
n=0.5
sumf05=(1+n*n)*(sump*sumr)/((n*n)*(sump)+sumr)
n=2
sumf2=(1+n*n)*(sump*sumr)/((n*n)*(sump)+sumr)
print("F1 - score  ", sumf1)
print("F0.5-score ", sumf05)
print("F2 -score ",sumf2)

F1 - score   0.928921712077252
F0.5-score  0.9296725853553282
F2 -score  0.9281720507434242


In [11]:
def FValues(precision , recall ,tagset, n):
  # return (1+n*n)*prec*recall
  fval={}
  for i in tagset:
    fval[i]=(1+n*n)*(precision[i]*recall[i])/((n*n)*(precision[i])+recall[i])
    # fval[i]=2*precision[i]*recall[i]/(precision[i]+recall[i])
  return fval

f1=FValues(prec,recall,list(tagset),1)
f2=FValues(prec,recall,list(tagset),2)
f05=FValues(prec,recall,list(tagset),0.5)



print(f1)
print(f2)
print(f05)
  




{'DET': 0.9430881639396256, 'NOUN': 0.9219369829698474, 'ADJ': 0.9016778926610186, 'VERB': 0.9362521991407848, 'ADP': 0.9245262106232337, '.': 0.9613002857304734, 'ADV': 0.8988001105427518, 'CONJ': 0.9661332156996544, 'PRT': 0.8090870886255694, 'PRON': 0.9380889235621437, 'NUM': 0.9266615472882688, 'X': 0.424211617218094}
{'DET': 0.9642735200001054, 'NOUN': 0.9074160478368843, 'ADJ': 0.8910491225837633, 'VERB': 0.92822912340073, 'ADP': 0.9367264875322633, '.': 0.9830159072281821, 'ADV': 0.8784620456569678, 'CONJ': 0.9625661260879986, 'PRT': 0.8168030947559328, 'PRON': 0.9256909904872016, 'NUM': 0.9086760622111456, 'X': 0.3404637704158935}
{'DET': 0.9228136917776267, 'NOUN': 0.936930218945621, 'ADJ': 0.9125632918655618, 'VERB': 0.944415177774315, 'ADP': 0.9126396497189257, '.': 0.9405233592046042, 'ADV': 0.9201022246628353, 'CONJ': 0.9697268415805108, 'PRT': 0.8015154981928893, 'PRON': 0.9508234599721999, 'NUM': 0.9453733848872752, 'X': 0.5626011998758317}


In [12]:
for i in tagset:
  print(i," : ",prec[i]," , ",recall[i]," , ",f1[i]," , ",f05[i]," , ",f2[i])

DET  :  0.90977484  ,  0.97893393  ,  0.9430881639396256  ,  0.9228136917776267  ,  0.9642735200001054
NOUN  :  0.9471996  ,  0.8979869  ,  0.9219369829698474  ,  0.936930218945621  ,  0.9074160478368843
ADJ  :  0.9199674  ,  0.8841014  ,  0.9016778926610186  ,  0.9125632918655618  ,  0.8910491225837633
VERB  :  0.9499367  ,  0.92295635  ,  0.9362521991407848  ,  0.944415177774315  ,  0.92822912340073
ADP  :  0.9048836  ,  0.94504046  ,  0.9245262106232337  ,  0.9126396497189257  ,  0.9367264875322633
.  :  0.92716396  ,  0.9980464  ,  0.9613002857304734  ,  0.9405233592046042  ,  0.9830159072281821
ADV  :  0.93487364  ,  0.8654071  ,  0.8988001105427518  ,  0.9201022246628353  ,  0.8784620456569678
CONJ  :  0.97213745  ,  0.96020263  ,  0.9661332156996544  ,  0.9697268415805108  ,  0.9625661260879986
PRT  :  0.796546  ,  0.82202935  ,  0.8090870886255694  ,  0.8015154981928893  ,  0.8168030947559328
PRON  :  0.959507  ,  0.9176062  ,  0.9380889235621437  ,  0.9508234599721999  ,  0.92

In [13]:
# posavg=np.array(per_pos_acc)
# pos_avg=np.sum(posavg,axis=0)/5
# print(conf_ma_avg.shape)
# conf_df = pd.DataFrame(pos_avg, columns = list(tagset),index=list(tagset))
# display(conf_df)
# print(posavg)


In [14]:
posavg=np.array(per_pos_acc)
# pos_avg=np.sum(posavg,axis=0)/5
# print(conf_ma_avg.shape)
# conf_df = pd.DataFrame(pos_avg, columns = list(tagset),index=list(tagset))
# display(conf_df)
# print(posavg)
d=dict(posavg[0])
acc=pd.DataFrame([d])
for i in range(1,5):
    acc=pd.concat([acc,pd.DataFrame([dict(posavg[i])])])
acc=pd.DataFrame(acc)
acc=acc.reset_index()
# print(d)
print(acc)

   index         ADP        PRON        VERB        NOUN           .  \
0      0   0.9208384  0.99572486  0.94426227  0.94849485  0.85031766   
1      0  0.92375696   0.9939138   0.9502876   0.9403495   0.8854046   
2      0  0.93727195   0.9950242  0.94452775    0.946644   0.8926495   
3      0  0.91328734   0.9933091   0.9542055  0.95082194   0.9585466   
4      0   0.8969955    0.997617   0.9545215  0.94410545   0.9702095   

          DET       CONJ         ADV         ADJ        PRT         NUM  \
0  0.93955976   0.990517   0.9148259  0.90780497  0.7287092  0.97586685   
1   0.9381591  0.9930612   0.9198695  0.90689343  0.7073131  0.96193165   
2  0.92690957  0.9928181   0.9339227   0.9177723  0.6695122  0.96738607   
3  0.88169783  0.9919477  0.92527694   0.9078271  0.7400269   0.9538754   
4    0.861262  0.9870561   0.9180993  0.87281924  0.7645212  0.87344915   

            X  
0  0.79710144  
1   0.5694444  
2   0.7853403  
3   0.7407407  
4   0.6603774  
